# Poetry with RNN

Today, we will generate poems. I love reading and writing poetry, so I thought it would be fun to see what a machine can come up with rather than my own mind. I'm using the [Gutenberg Poetry Corpus by Allison Parris](https://github.com/aparrish/gutenberg-poetry-corpus).

This is mostly a learning exercise and practice document for me. Hope you enjoy the read.

#### Recurrent Neural Network (RNN)
A recurrent neural network is a network with loops in it, which allows previous outputs to be used as inputs to the current step while having a hidden state. The hidden state remembers some information about a sequence. It can be understood as multiple copies of the same network that each pass a message to the next network.

For more details, [visit this Medium article by Suvro Banerjee](https://medium.com/explore-artificial-intelligence/an-introduction-to-recurrent-neural-networks-72c97bf0912).

#### Long Short-Term Memory (LSTM) Networks
RNNs fail to understand the context behind input because they only remember things for short durations of time. Therefore once a lot of words are fed in, information gets lost and predictions are less reliable. This is because of the Vanishing Gradient problem: as more layers using the sigmoid activation function (or others) are added to neural networks, the gradients of the loss function approach 0. It becomes difficult to train layers. Read more about it [on Towards Data Science](https://towardsdatascience.com/the-vanishing-gradient-problem-69bf08b15484).

We can use LSTM Networks, a version of a RNN, to fix this issue. With LSTMs, information flows through cell states, allowing for slight modification of information -- LSTMs can therefore selectively remember or forget things.

## Prepare Data

In [5]:
import json
import random
import numpy as np
#import pandas as pd

all_lines = []
#for line in open("../input/sew-v1/sew_file_01_V1.txt"):
#    print(line.strip())
#    all_lines.append(json.loads(line.strip()))

In [7]:
#corpus = "\n".join([line['s'] for line in random.sample(all_lines, 1000)])
#corpus = open("../input/sew-v1/sew_file_01_V1.txt")
f = open("datasets/sew_file_01_V1.txt", "r",encoding="utf8")
#print(f.read())
#corpus = "\n".join([line['s'] for line in all_lines])
corpus = f.read()
print(corpus)

දෑසම රිද්දන හසගන තාලෙට 
පාද නගාගෙන කවුද හැබෑටම
මේ යන රන් ළන්ඳා
කිව්වානාහන මේ මගෙ දෑසම 
ඇසිපිය නොහෙළනවා

මේ හැටි ලස්සන රූ වරුනාවට 
ඉබේම නැවතුනු හිටි පාදෙම
ඔය කී රූ වරුණා
මා ගැන නම් මේ අහන්න ආසයි 
ආයෙම මයෙ වරුණා   

මල් පෙති වාගේ පාද රිදෙද්දෝ 
බොරළු ප‍යේ ඇනිලා
මා‍ ගැන මන්දෝ මේ අනුකම්පා 
හිතට දුකක් දැනිලා
ආලේ කුසුමෙන් මා හිත පිපිලා 
සුවඳ හදේ රැඳිලා

දෑසම රිද්දන හසගන තාලෙට 
පාද නගාගෙන කවුද හැබෑටම
මේ යන රන් ළන්ඳා
මා ගැන නම් මේ අහන්න ආසයි 
ආයෙම මයෙ වරුණා   

පේරද නාරං බෝවිටියා දං 
අපට කඩා දෙයිදෝ
බුරුතු පිටින් මේ වාරේ අවාරේ 
නෙලාන ඉන්නම් දෝ
මේ ගුරු පා‍රේ මේ නෙතු ආයේ 
හෙටත් සිනා සෙයිදෝ

දෑසම රිද්දන හසගන තාලෙට 
පාද නගාගෙන කවුද හැබෑටම
මේ යන රන් ළන්ඳා
කිව්වානාහන මේ මගෙ දෑසම 
ඇසිපිය නොහෙළනවා

මේ හැටි ලස්සන රූ වරුනාවට 
ඉබේම නැවතුනු හිටි පාදෙම
ඔය කී රූ වරුණා
මා ගැන නම් මේ අහන්න ආසයි 
ආයෙම මයෙ වරුණා   




ආදර සැමරුම් කැටිවූ 
නෙතු කඳුළින් මුතුපබළු
නිමා කළෙමි සිහිවටනය
යමුනා තීරේ..යමුනා තීරේ
ආදර සැමරුම් කැටිවූ 
නෙතු කඳුළින් මුතුපබළු
නිමා කළෙමි සිහිවටනය
යමුනා තීරේ..යමුනා තීරේ
එවන් නිමල මැදුර බලා වඩින්න 

## Aside: Markov chain text generation

Markov chains generate sentences based on recombination of elements of known sentences: it analyzes the words and the probability of occurence of two consecutive words. The generation is randomized and based on the probability of each words.

Let's generate a poem with this method, and then continue with our RNN method to see how they compare.

In [ ]:
import markovify

In [ ]:
model = markovify.NewlineText(corpus)

In [ ]:
for i in range(5):
    print()
    for i in range(random.randrange(1, 4)):
        print(model.make_short_sentence(30))

## Character-Level LSTM Text Generation

#### Import Libraries

In [16]:
from keras.layers import LSTM, Dense, Dropout, Flatten
from keras.callbacks import LambdaCallback
from keras.models import Sequential
from keras.optimizers import RMSprop
from keras.utils import np_utils

Using TensorFlow backend.


#### Prepare Text

In [18]:
# Lowercase all text
text = corpus.lower()

chars = list(set(text))
print(chars)
char_indices = dict((c, i) for i, c in enumerate(chars))
print(char_indices)
indices_char = dict((i, c) for i, c in enumerate(chars))
print(indices_char)

vocab_size = len(chars)
print('Vocabulary size: {}'.format(vocab_size))

['ඝ', 'ැ', 'ඩ', 'e', 'ඹ', 's', 'ළ', 'භ', 'ක', 'ඔ', 'ො', 'd', 'ශ', 'ු', 'ඕ', 'ථ', 'ඬ', 'p', 'v', 'ඇ', 'ණ', 'ජ', '\u200c', 'ෙ', 'b', 'g', 'ර', 'ෞ', 'f', ' ', 'ධ', 'i', 'ේ', 'එ', 'o', 'ා', 'ෛ', 'ට', 'ඛ', 'ආ', 'ඒ', 'ග', 'ඟ', 'බ', 'ද', 'ස', 'ප', 'ඳ', '\t', 'න', 'n', 'ත', 'm', 'ය', 'h', 'a', 'ඈ', 't', '.', 'ං', 'ව', 'හ', "'", 'r', 'අ', 'w', ',', 'ූ', '්', '\u200d', 'ෘ', 'උ', 'ඵ', 'ම', '-', 'ල', '\n', 'ි', 'ඉ', 'ී', 'ෑ', 'ච', 'ෝ', 'ඊ', 'l', 'y', 'ෂ']
{'ඝ': 0, 'ැ': 1, 'ඩ': 2, 'e': 3, 'ඹ': 4, 's': 5, 'ළ': 6, 'භ': 7, 'ක': 8, 'ඔ': 9, 'ො': 10, 'd': 11, 'ශ': 12, 'ු': 13, 'ඕ': 14, 'ථ': 15, 'ඬ': 16, 'p': 17, 'v': 18, 'ඇ': 19, 'ණ': 20, 'ජ': 21, '\u200c': 22, 'ෙ': 23, 'b': 24, 'g': 25, 'ර': 26, 'ෞ': 27, 'f': 28, ' ': 29, 'ධ': 30, 'i': 31, 'ේ': 32, 'එ': 33, 'o': 34, 'ා': 35, 'ෛ': 36, 'ට': 37, 'ඛ': 38, 'ආ': 39, 'ඒ': 40, 'ග': 41, 'ඟ': 42, 'බ': 43, 'ද': 44, 'ස': 45, 'ප': 46, 'ඳ': 47, '\t': 48, 'න': 49, 'n': 50, 'ත': 51, 'm': 52, 'ය': 53, 'h': 54, 'a': 55, 'ඈ': 56, 't': 57, '.': 58, 'ං': 59, 'ව': 60, 'හ': 6

#### Prepare Data

In [19]:
# Data preparation
X = [] # training array
Y = [] # target array

length = len(text)
seq_length = 25 # number of characters to consider before predicting a character

# Iterate over length of text and create sequences stored in X, true values stored in Y
# true values being which character would actually come after sequence stored in X
for i in range(0, length - seq_length, 1):
    sequence = text[i:i + seq_length]
    print('sequence'+sequence)
    label = text[i + seq_length]
    print('label'+label)
    X.append([char_indices[char] for char in sequence])
    Y.append(char_indices[label])

print('Number of sequences: {}'.format(len(X)))
#print(X[100])
print('--------------')
#print(Y[100])

sequenceදෑසම රිද්දන හසගන තාල
labelෙ
sequenceෑසම රිද්දන හසගන තාලෙ
labelට
sequenceසම රිද්දන හසගන තාලෙට
label 
sequenceම රිද්දන හසගන තාලෙට 
label

sequence රිද්දන හසගන තාලෙට 

labelප
sequenceරිද්දන හසගන තාලෙට 
ප
labelා
sequenceිද්දන හසගන තාලෙට 
පා
labelද
sequenceද්දන හසගන තාලෙට 
පාද
label 
sequence්දන හසගන තාලෙට 
පාද 
labelන
sequenceදන හසගන තාලෙට 
පාද න
labelග
sequenceන හසගන තාලෙට 
පාද නග
labelා
sequence හසගන තාලෙට 
පාද නගා
labelග
sequenceහසගන තාලෙට 
පාද නගාග
labelෙ
sequenceසගන තාලෙට 
පාද නගාගෙ
labelන
sequenceගන තාලෙට 
පාද නගාගෙන
label 
sequenceන තාලෙට 
පාද නගාගෙන 
labelක
sequence තාලෙට 
පාද නගාගෙන ක
labelව
sequenceතාලෙට 
පාද නගාගෙන කව
labelු
sequenceාලෙට 
පාද නගාගෙන කවු
labelද
sequenceලෙට 
පාද නගාගෙන කවුද
label 
sequenceෙට 
පාද නගාගෙන කවුද 
labelහ
sequenceට 
පාද නගාගෙන කවුද හ
labelැ
sequence 
පාද නගාගෙන කවුද හැ
labelබ
sequence
පාද නගාගෙන කවුද හැබ
labelෑ
sequenceපාද නගාගෙන කවුද හැබෑ
labelට
sequenceාද නගාගෙන කවුද හැබෑට
labelම
sequenceද නගාගෙන කවුද හැබෑටම
label

sequence නගාගෙන කවුද හැබෑටම


ඉබේම න
labelැ
sequence රූ වරුනාවට 
ඉබේම නැ
labelව
sequenceරූ වරුනාවට 
ඉබේම නැව
labelත
sequenceූ වරුනාවට 
ඉබේම නැවත
labelු
sequence වරුනාවට 
ඉබේම නැවතු
labelන
sequenceවරුනාවට 
ඉබේම නැවතුන
labelු
sequenceරුනාවට 
ඉබේම නැවතුනු
label 
sequenceුනාවට 
ඉබේම නැවතුනු 
labelහ
sequenceනාවට 
ඉබේම නැවතුනු හ
labelි
sequenceාවට 
ඉබේම නැවතුනු හි
labelට
sequenceවට 
ඉබේම නැවතුනු හිට
labelි
sequenceට 
ඉබේම නැවතුනු හිටි
label 
sequence 
ඉබේම නැවතුනු හිටි 
labelප
sequence
ඉබේම නැවතුනු හිටි ප
labelා
sequenceඉබේම නැවතුනු හිටි පා
labelද
sequenceබේම නැවතුනු හිටි පාද
labelෙ
sequenceේම නැවතුනු හිටි පාදෙ
labelම
sequenceම නැවතුනු හිටි පාදෙම
label

sequence නැවතුනු හිටි පාදෙම

labelඔ
sequenceනැවතුනු හිටි පාදෙම
ඔ
labelය
sequenceැවතුනු හිටි පාදෙම
ඔය
label 
sequenceවතුනු හිටි පාදෙම
ඔය 
labelක
sequenceතුනු හිටි පාදෙම
ඔය ක
labelී
sequenceුනු හිටි පාදෙම
ඔය කී
label 
sequenceනු හිටි පාදෙම
ඔය කී 
labelර
sequenceු හිටි පාදෙම
ඔය කී ර
labelූ
sequence හිටි පාදෙම
ඔය කී රූ
label 
sequenceහිටි පාදෙම
ඔය කී රූ 
labelව
sequenceිටි පා

sequence

ආදර සැමරුම් කැටිවූ
label 
sequence
ආදර සැමරුම් කැටිවූ 
label

sequenceආදර සැමරුම් කැටිවූ 

labelන
sequenceදර සැමරුම් කැටිවූ 
න
labelෙ
sequenceර සැමරුම් කැටිවූ 
නෙ
labelත
sequence සැමරුම් කැටිවූ 
නෙත
labelු
sequenceසැමරුම් කැටිවූ 
නෙතු
label 
sequenceැමරුම් කැටිවූ 
නෙතු 
labelක
sequenceමරුම් කැටිවූ 
නෙතු ක
labelඳ
sequenceරුම් කැටිවූ 
නෙතු කඳ
labelු
sequenceුම් කැටිවූ 
නෙතු කඳු
labelළ
sequenceම් කැටිවූ 
නෙතු කඳුළ
labelි
sequence් කැටිවූ 
නෙතු කඳුළි
labelන
sequence කැටිවූ 
නෙතු කඳුළින
label්
sequenceකැටිවූ 
නෙතු කඳුළින්
label 
sequenceැටිවූ 
නෙතු කඳුළින් 
labelම
sequenceටිවූ 
නෙතු කඳුළින් ම
labelු
sequenceිවූ 
නෙතු කඳුළින් මු
labelත
sequenceවූ 
නෙතු කඳුළින් මුත
labelු
sequenceූ 
නෙතු කඳුළින් මුතු
labelප
sequence 
නෙතු කඳුළින් මුතුප
labelබ
sequence
නෙතු කඳුළින් මුතුපබ
labelළ
sequenceනෙතු කඳුළින් මුතුපබළ
labelු
sequenceෙතු කඳුළින් මුතුපබළු
label

sequenceතු කඳුළින් මුතුපබළු

labelන
sequenceු කඳුළින් මුතුපබළු
න
labelි
sequence කඳුළින් මුතුපබළු
නි
labelම
sequenceකඳුළින් මුතුපබළු
නිම

labelට
sequenceලා වඩින්න දේවියේ
හෙට
label 
sequenceා වඩින්න දේවියේ
හෙට 
labelද
sequence වඩින්න දේවියේ
හෙට ද
labelි
sequenceවඩින්න දේවියේ
හෙට දි
labelන
sequenceඩින්න දේවියේ
හෙට දින
label 
sequenceින්න දේවියේ
හෙට දින 
labelම
sequenceන්න දේවියේ
හෙට දින ම
labelා
sequence්න දේවියේ
හෙට දින මා
label 
sequenceන දේවියේ
හෙට දින මා 
labelඑ
sequence දේවියේ
හෙට දින මා එ
labelන
sequenceදේවියේ
හෙට දින මා එන
labelත
sequenceේවියේ
හෙට දින මා එනත
labelු
sequenceවියේ
හෙට දින මා එනතු
labelර
sequenceියේ
හෙට දින මා එනතුර
labelු
sequenceයේ
හෙට දින මා එනතුරු
label 
sequenceේ
හෙට දින මා එනතුරු 
labelඑ
sequence
හෙට දින මා එනතුරු එ
labelහ
sequenceහෙට දින මා එනතුරු එහ
labelි
sequenceෙට දින මා එනතුරු එහි
label 
sequenceට දින මා එනතුරු එහි 
labelන
sequence දින මා එනතුරු එහි න
labelි
sequenceදින මා එනතුරු එහි නි
labelද
sequenceින මා එනතුරු එහි නිද
labelන
sequenceන මා එනතුරු එහි නිදන
label්
sequence මා එනතුරු එහි නිදන්
labelන
sequenceමා එනතුරු එහි නිදන්න
label 
sequenceා එනතුරු එහි නිදන්න 
labelද
sequence එනතුරු එහි න

label්
sequenceණා නම්

සමුගන්නට නම්
label 
sequenceා නම්

සමුගන්නට නම් 
labelඅ
sequence නම්

සමුගන්නට නම් අ
labelහ
sequenceනම්

සමුගන්නට නම් අහ
labelි
sequenceම්

සමුගන්නට නම් අහි
labelම
sequence්

සමුගන්නට නම් අහිම
labelි
sequence

සමුගන්නට නම් අහිමි
label 
sequence
සමුගන්නට නම් අහිමි 
labelආ
sequenceසමුගන්නට නම් අහිමි ආ
labelද
sequenceමුගන්නට නම් අහිමි ආද
labelර
sequenceුගන්නට නම් අහිමි ආදර
labelෙ
sequenceගන්නට නම් අහිමි ආදරෙ
labelන
sequenceන්නට නම් අහිමි ආදරෙන
label්
sequence්නට නම් අහිමි ආදරෙන්
label

sequenceනට නම් අහිමි ආදරෙන්

labelආ
sequenceට නම් අහිමි ආදරෙන්
ආ
labelය
sequence නම් අහිමි ආදරෙන්
ආය
labelෙ
sequenceනම් අහිමි ආදරෙන්
ආයෙ
labelත
sequenceම් අහිමි ආදරෙන්
ආයෙත
label්
sequence් අහිමි ආදරෙන්
ආයෙත්
label 
sequence අහිමි ආදරෙන්
ආයෙත් 
labelඇ
sequenceඅහිමි ආදරෙන්
ආයෙත් ඇ
labelය
sequenceහිමි ආදරෙන්
ආයෙත් ඇය
labelි
sequenceිමි ආදරෙන්
ආයෙත් ඇයි
label 
sequenceමි ආදරෙන්
ආයෙත් ඇයි 
labelඅ
sequenceි ආදරෙන්
ආයෙත් ඇයි අ
labelප
sequence ආදරෙන්
ආයෙත් ඇයි අප
label 
sequenceආදරෙන්
ආයෙත් 

...

sequence නංවලා මල් පීදිලා
ඔබ
labelෙ
sequenceනංවලා මල් පීදිලා
ඔබෙ
label 
sequenceංවලා මල් පීදිලා
ඔබෙ 
labelප
sequenceවලා මල් පීදිලා
ඔබෙ ප
labelෙ
sequenceලා මල් පීදිලා
ඔබෙ පෙ
labelම
sequenceා මල් පීදිලා
ඔබෙ පෙම
label්
sequence මල් පීදිලා
ඔබෙ පෙම්
label 
sequenceමල් පීදිලා
ඔබෙ පෙම් 
labelස
sequenceල් පීදිලා
ඔබෙ පෙම් ස
labelු
sequence් පීදිලා
ඔබෙ පෙම් සු
labelව
sequence පීදිලා
ඔබෙ පෙම් සුව
labelේ
sequenceපීදිලා
ඔබෙ පෙම් සුවේ
label 
sequenceීදිලා
ඔබෙ පෙම් සුවේ 
labelම
sequenceදිලා
ඔබෙ පෙම් සුවේ ම
labelා
sequenceිලා
ඔබෙ පෙම් සුවේ මා
label 
sequenceලා
ඔබෙ පෙම් සුවේ මා 
labelස
sequenceා
ඔබෙ පෙම් සුවේ මා ස
labelො
sequence
ඔබෙ පෙම් සුවේ මා සො
labelය
sequenceඔබෙ පෙම් සුවේ මා සොය
labelා
sequenceබෙ පෙම් සුවේ මා සොයා
label

sequenceෙ පෙම් සුවේ මා සොයා

label

sequence පෙම් සුවේ මා සොයා


labelර
sequenceපෙම් සුවේ මා සොයා

ර
labelු
sequenceෙම් සුවේ මා සොයා

රු
labelද
sequenceම් සුවේ මා සොයා

රුද
labelු
sequence් සුවේ මා සොයා

රුදු
labelර
sequence සුවේ මා සොයා

රුදුර
labelු
sequenceසුවේ මා සොයා

රුදුරු

label 
sequenceූ තැන හිඳ
වෙන්වන්නට 
labelම
sequence තැන හිඳ
වෙන්වන්නට ම
labelු
sequenceතැන හිඳ
වෙන්වන්නට මු
labelණ
sequenceැන හිඳ
වෙන්වන්නට මුණ
label 
sequenceන හිඳ
වෙන්වන්නට මුණ 
labelග
sequence හිඳ
වෙන්වන්නට මුණ ග
labelැ
sequenceහිඳ
වෙන්වන්නට මුණ ගැ
labelස
sequenceිඳ
වෙන්වන්නට මුණ ගැස
labelෙ
sequenceඳ
වෙන්වන්නට මුණ ගැසෙ
labelම
sequence
වෙන්වන්නට මුණ ගැසෙම
labelු
sequenceවෙන්වන්නට මුණ ගැසෙමු
label 
sequenceෙන්වන්නට මුණ ගැසෙමු 
labelය
sequenceන්වන්නට මුණ ගැසෙමු ය
labelළ
sequence්වන්නට මුණ ගැසෙමු යළ
labelි
sequenceවන්නට මුණ ගැසෙමු යළි
label

sequenceන්නට මුණ ගැසෙමු යළි

labelව
sequence්නට මුණ ගැසෙමු යළි
ව
labelෙ
sequenceනට මුණ ගැසෙමු යළි
වෙ
labelර
sequenceට මුණ ගැසෙමු යළි
වෙර
labelළ
sequence මුණ ගැසෙමු යළි
වෙරළ
label 
sequenceමුණ ගැසෙමු යළි
වෙරළ 
labelක
sequenceුණ ගැසෙමු යළි
වෙරළ ක
labelො
sequenceණ ගැසෙමු යළි
වෙරළ කො
labelන
sequence ගැසෙමු යළි
වෙරළ කොන
labelක
sequenceගැසෙමු යළි
වෙරළ කොනක
label 
sequenceැසෙමු යළි
වෙරළ කොනක 
labelහ
sequenceසෙමු යළි
වෙරළ කොනක හ
labelි
sequenceෙමු යළි
වෙරළ 

labelැ
sequenceර දිනයක අප හමු වූ තැ
labelන
sequence දිනයක අප හමු වූ තැන
label 
sequenceදිනයක අප හමු වූ තැන 
labelහ
sequenceිනයක අප හමු වූ තැන හ
labelි
sequenceනයක අප හමු වූ තැන හි
labelඳ
sequenceයක අප හමු වූ තැන හිඳ
label

sequenceක අප හමු වූ තැන හිඳ

labelව
sequence අප හමු වූ තැන හිඳ
ව
labelෙ
sequenceඅප හමු වූ තැන හිඳ
වෙ
labelන
sequenceප හමු වූ තැන හිඳ
වෙන
label්
sequence හමු වූ තැන හිඳ
වෙන්
labelව
sequenceහමු වූ තැන හිඳ
වෙන්ව
labelන
sequenceමු වූ තැන හිඳ
වෙන්වන
label්
sequenceු වූ තැන හිඳ
වෙන්වන්
labelන
sequence වූ තැන හිඳ
වෙන්වන්න
labelට
sequenceවූ තැන හිඳ
වෙන්වන්නට
label 
sequenceූ තැන හිඳ
වෙන්වන්නට 
labelම
sequence තැන හිඳ
වෙන්වන්නට ම
labelු
sequenceතැන හිඳ
වෙන්වන්නට මු
labelණ
sequenceැන හිඳ
වෙන්වන්නට මුණ
labelග
sequenceන හිඳ
වෙන්වන්නට මුණග
labelැ
sequence හිඳ
වෙන්වන්නට මුණගැ
labelස
sequenceහිඳ
වෙන්වන්නට මුණගැස
labelෙ
sequenceිඳ
වෙන්වන්නට මුණගැසෙ
labelම
sequenceඳ
වෙන්වන්නට මුණගැසෙම
labelු
sequence
වෙන්වන්නට මුණගැසෙමු
label 
sequenceවෙන්වන්නට මුණගැසෙමු 
labelය
sequenceෙන්වන්නට මුණග

යහනේ 
labelස
sequenceශෝකෙන් වෙලිලා
යහනේ ස
labelැ
sequenceෝකෙන් වෙලිලා
යහනේ සැ
labelත
sequenceකෙන් වෙලිලා
යහනේ සැත
labelප
sequenceෙන් වෙලිලා
යහනේ සැතප
labelේ
sequenceන් වෙලිලා
යහනේ සැතපේ
labelද
sequence් වෙලිලා
යහනේ සැතපේද
labelෝ
sequence වෙලිලා
යහනේ සැතපේදෝ
label

sequenceවෙලිලා
යහනේ සැතපේදෝ

labelඅ
sequenceෙලිලා
යහනේ සැතපේදෝ
අ
labelර
sequenceලිලා
යහනේ සැතපේදෝ
අර
labelු
sequenceිලා
යහනේ සැතපේදෝ
අරු
labelන
sequenceලා
යහනේ සැතපේදෝ
අරුන
labelළ
sequenceා
යහනේ සැතපේදෝ
අරුනළ
labelු
sequence
යහනේ සැතපේදෝ
අරුනළු
label 
sequenceයහනේ සැතපේදෝ
අරුනළු 
labelඋ
sequenceහනේ සැතපේදෝ
අරුනළු උ
labelද
sequenceනේ සැතපේදෝ
අරුනළු උද
labelා
sequenceේ සැතපේදෝ
අරුනළු උදා
labelව
sequence සැතපේදෝ
අරුනළු උදාව
labelෙ
sequenceසැතපේදෝ
අරුනළු උදාවෙ
labelල
sequenceැතපේදෝ
අරුනළු උදාවෙල
labelා
sequenceතපේදෝ
අරුනළු උදාවෙලා
label

sequenceපේදෝ
අරුනළු උදාවෙලා

labelම
sequenceේදෝ
අරුනළු උදාවෙලා
ම
labelු
sequenceදෝ
අරුනළු උදාවෙලා
මු
labelව
sequenceෝ
අරුනළු උදාවෙලා
මුව
label 
sequence
අරුනළු උදාවෙලා
මුව 
labelව
sequenceඅරුනළු 

sequenceආව ඔයාම
ආදරයේ දුක දී
labelල
sequenceව ඔයාම
ආදරයේ දුක දීල
labelා
sequence ඔයාම
ආදරයේ දුක දීලා
label 
sequenceඔයාම
ආදරයේ දුක දීලා 
labelග
sequenceයාම
ආදරයේ දුක දීලා ග
labelි
sequenceාම
ආදරයේ දුක දීලා ගි
labelය
sequenceම
ආදරයේ දුක දීලා ගිය
labelා
sequence
ආදරයේ දුක දීලා ගියා
labelන
sequenceආදරයේ දුක දීලා ගියාන
labelෙ
sequenceදරයේ දුක දීලා ගියානෙ
label 
sequenceරයේ දුක දීලා ගියානෙ 
labelඈ
sequenceයේ දුක දීලා ගියානෙ ඈ
labelත
sequenceේ දුක දීලා ගියානෙ ඈත
label

sequence දුක දීලා ගියානෙ ඈත

labelළ
sequenceදුක දීලා ගියානෙ ඈත
ළ
labelඟ
sequenceුක දීලා ගියානෙ ඈත
ළඟ
label 
sequenceක දීලා ගියානෙ ඈත
ළඟ 
labelන
sequence දීලා ගියානෙ ඈත
ළඟ න
labelැ
sequenceදීලා ගියානෙ ඈත
ළඟ නැ
labelත
sequenceීලා ගියානෙ ඈත
ළඟ නැත
labelු
sequenceලා ගියානෙ ඈත
ළඟ නැතු
labelව
sequenceා ගියානෙ ඈත
ළඟ නැතුව
labelට
sequence ගියානෙ ඈත
ළඟ නැතුවට
label 
sequenceගියානෙ ඈත
ළඟ නැතුවට 
labelහ
sequenceියානෙ ඈත
ළඟ නැතුවට හ
labelි
sequenceයානෙ ඈත
ළඟ නැතුවට හි
labelම
sequenceානෙ ඈත
ළඟ නැතුවට හිම
labelි
sequenceනෙ ඈත
ළඟ නැතුවට හිමි

In [20]:
# Reshape dimensions
X_new = np.reshape(X, (len(X), seq_length, 1))
# Scale values
X_new = X_new/float(len(chars))
# One-hot encode Y to remove ordinal relationships
Y_new = np_utils.to_categorical(Y)

X_new.shape, Y_new.shape

((93855, 20, 1), (93855, 87))

#### Create Model

In [21]:
model = Sequential()
# Add LSTM layer to compute output using 150 LSTM units
model.add(LSTM(150, input_shape = (X_new.shape[1], X_new.shape[2]), return_sequences = True))

# Add regularization layer to prevent overfitting.
# Dropout ignores randomly selected neurons during training ("dropped out").
# Ultimately, network becomes less sensitive to specific weights of neurons --> network is better at generalization.
model.add(Dropout(0.1))

model.add(Flatten())
# Dense layer with softmax activation function to approximate probability distribution of next best word
model.add(Dense(Y_new.shape[1], activation = 'softmax'))

# Compile model to configure learning process
# Categorical crossentropy: an example can only belong to one class
# Adam optimization algorithm updates a learning rate for each network weight iteratively as learning unfolds
model.compile(loss = 'categorical_crossentropy', optimizer = 'adam')

# Use 1 epoch for sake of computational time
model.fit(X_new, Y_new, epochs = 10, verbose = 1)

Epoch 1/1
93855/93855 [==============================] - 130s 1ms/step - loss: 3.3133


#### Generate Text

In [22]:
# Random start
start = np.random.randint(0, len(X)-1)
string_mapped = list(X[start])
full_string = [indices_char[value] for value in string_mapped]

# Generate text
for i in range(400):
    x = np.reshape(string_mapped, (1, len(string_mapped), 1))
    x = x / float(len(chars))
    
    pred_index = np.argmax(model.predict(x, verbose = 0))
    seq = [indices_char[value] for value in string_mapped]
    full_string.append(indices_char[pred_index])
    
    string_mapped.append(pred_index)
    string_mapped = string_mapped[1:len(string_mapped)]
    
# Combine text
newtext = ''
for char in full_string:
    newtext = newtext + char

print(newtext)

මේ පාට තමයි
දේදුන්න                                                                                                                                                                                                                                                                                                                                                                                                                


## Predicting Next Words

In [ ]:
import keras.utils as ku
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.layers import Embedding

# Lowercase all text
text = corpus.lower()
text = text.split('\n')

# Create Tokenizer object to convert words to sequences of integers
tokenizer = Tokenizer(num_words = None, filters = '#$%&()*+-<=>@[\\]^_`{|}~\t\n', lower = False)

# Train tokenizer to the texts
tokenizer.fit_on_texts(text)
total_words = len(tokenizer.word_index) + 1

# Convert list of strings into flat dataset of sequences of tokens
sequences = []
for line in text:
    token_list = tokenizer.texts_to_sequences([line])[0]
    for i in range(1, len(token_list)):
        n_gram_sequence = token_list[:i+1]
        sequences.append(n_gram_sequence)

# Pad sequences to ensure equal lengths
max_seq_len = max([len(x) for x in sequences])
sequences = np.array(pad_sequences(sequences, maxlen = max_seq_len, padding = 'pre'))

# Create n-grams sequence predictors and labels
predictors, label = sequences[:, :-1], sequences[:, -1]
label = ku.to_categorical(label, num_classes = total_words)

#### Create Model

In [ ]:
# Input layer takes sequence of words as input
input_len = max_seq_len - 1
model = Sequential()
model.add(Embedding(total_words, 10, input_length = input_len))
model.add(LSTM(150))
model.add(Dropout(0.1))
model.add(Dense(total_words, activation = 'softmax'))
model.compile(loss = 'categorical_crossentropy', optimizer = 'adam')

# Use 100 epoch for efficacy
model.fit(predictors, label, epochs = 100, verbose = 1)

In [ ]:
# Function to generate line
def generate_line(text, next_words, max_seq_len, model):
    for j in range(next_words):
        token_list = tokenizer.texts_to_sequences([text])[0]
        token_list = pad_sequences([token_list], maxlen = max_seq_len - 1, padding = 'pre')
        predicted = model.predict_classes(token_list, verbose = 0)
        
        output_word = ''
        for word, index in tokenizer.word_index.items():
            if index == predicted:
                output_word = word
                break
        text += ' ' + output_word
    return text

In [ ]:
generate_line("gone were the", 5, max_seq_len, model)

In [ ]:
generate_line("oh what sweet", 5, max_seq_len, model)

##### Thank you!